<center><h2> MD Simulation of Particles in Box</h2></center>

""" From "COMPUTATIONHL PHYSICS" & "COMPUTER PROBLEMS in PHYSICS" by RH Landau, MJ Paez, and CC Bordeianu (deceased). Copyright R Landau, Oregon State Unv, MJ Paez, Univ Antioquia, C Bordeianu, Univ Bucharest, 2020. Please respect copyright & acknowledge our work."""

<p> An MD simulation of 16 particles in a box with  Lennard-Jones potentials.

In [ ]:
# Velocity distribution of particles in a box
from vpython import *
import random
import numpy as np

In [ ]:
L = 1                                # box side 
minix = 2.0                          # min velocity
maxix = 6.0                          # max velocity
scene  =  canvas(width = 500,height = 500,range = (1.3)  )
inside = label(pos = vec(0.4,1.1,0),text = 'Particles here = ',box = 0)
inside2 = label(pos = vec(0.8,1.1,0),box = 0)
Natom = 16                                 
Nr = 0                                # number particles right side
dt = 1e-6                             # time step
border = curve(pos = [(-L,-L,0),(L,-L,0),(L,L,0),(-L,L,0),(-L,-L,0)]) #limits figure
half = curve(pos = [(0,-L,0),(0,L,0)],color = color.yellow)       # middle
ndist  =  graph(ymax  =  30000,xmin = 4,xmax = 5,
             width = 400, height = 300, xtitle = 'Velocity distribution', ytitle = 'N')
bars = gvbars(delta = 0.05,color = color.red)
positions = []                           # position of atoms
vel = []                                 # vel of atoms
Atom = []                                # for atom spheres
dv = []                                  # for RHS atoms
fr = np.zeros(Natom)                     # atoms' force 
fr2 = np.zeros(Natom)                    # second force
Ratom = 0.03 
ar = Ratom                               # radius of atom
vini = 4.5                               # a reference velocity
h = 0.04
factor = 1e-11                           # for lennard jones

In [ ]:
for i in range (0,Natom):              # initial positions and velocities
    col = vec(1.3*random.random(),1.3*random.random(),1.3*random.random())
    x = 2.*(L-ar)*random.random()-L+Ratom     # positons of atoms
    y = 2.*(L-ar)*random.random()-L+Ratom     # border forbidden
    Atom = Atom+[sphere(pos = vec(x,y,0),radius = ar,color = col)] # add atoms
    theta = 2*pi*random.random()         # select angle  0< = theta< =  2pi
    vx = vini*cos(theta)                 # x component velocity
    vy = vini*sin(theta)
    positions.append((x,y,0))            # add positions to list
    vel.append((vx,vy,0))                # add momentum to list
    posi = np.array(positions)               # array with positions
    ddp = posi[i]
    if ddp[0]> = 0 and ddp[0]< = L:        # count initial atoms at right half
           Nr+ = 1    
    v = np.array(vel)                       # array of velocities
    
def sign(a, b):                        # sign function
    if (b > =   0.0): return abs(a)
    else:             return -abs(a)

In [ ]:
def forces(fr):          
     fr = [0]*(Natom)
     for i in range( 0, Natom-1 ):
          for j in range(i + 1, Natom):
              dr = posi[i]-posi[j]          # relative position between particles
              if (abs(dr[0]) > L):       # smallest distance from part or image
                  dr[0]  =  dr[0]  -  sign(2*L, dr[0])  # interact with closest image
              if (abs(dr[1]) > L):       # same for y
                  dr[1]  =  dr[1]  -  sign(2*L, dr[1])
              r2 = dr[0]**2 + dr[1]**2 + dr[2]**2                
              if abs(r2) < Ratom:       # to avoid 0 denominator
                  #print('      ',r2)
                  r2  =  Ratom              # (minimum distance between 2 atoms)**2
              invr2  =  1./r2               
              fij  = invr2*factor*  48.*(invr2**3 - 0.5) *invr2**3 #
              fr[i] = fij*dr+ fr[i]
              fr[j] = -fij*dr +fr[j]       # lennard jones force
     return fr       

In [ ]:
histo = np.zeros(11)
for t in range (0,4000):                 # time steps
     Nr=0  
     if t%500==0: print('t ',t)
     for i in range(0,Natom):
        rate(500)
        fr = forces(fr)
        dpos = posi[i]
        if dpos[0] <= -L: posi[i] = [dpos[0]+2*L,dpos[1],0] # x PBC
        if dpos[0] >= L:  posi[i] = [dpos[0]-2*L,dpos[1],0]
        if dpos[1] <= -L: posi[i] = [dpos[0],dpos[1]+2*L,0] # y PBC
        if dpos[1] >= L:  posi[i] = [dpos[0],dpos[1]-2*L,0]
        dpos=posi[i]
        if dpos[0]>0 and dpos[0]<L:   Nr += 1  # count particles at right
        fr2 = forces(fr)
        fr2 = fr
        v[i] = v[i]+0.5*h*h*(fr[i]+fr2[i])       # velocity Verlet algorithm
        bb = v[i]
        posi[i] = posi[i]+h*v[i]+0.5*h*h*fr[i]
        aa = posi[i]
        Atom[i].pos = vec(aa[0], aa[1],aa[2])   # plot atoms at new positions
        dvel = int(np.sqrt(bb[0]**2+bb[1]**2+bb[2]**2)*10)/10
        dev = int(dvel*10)-40
        histo[dev] += 1  #histo[0]-> v=4.0, histo[1]->4.1
        bars.plot(dvel,histo[dev])
     inside2.text='%4s'%Nr                      # particles in right side
print("finished")